Check that A does not imply B by finding a model of A&C not satisfying B, for some C

In [1]:
import subprocess
import itertools
import find_equation_id
import time

In [2]:
MACE4 = "/home/josebrox/LADR-2009-11A/bin/mace4"
PROVER9 = "/home/josebrox/LADR-2009-11A/bin/prover9"

In [3]:
def implicationtoeq(eqclause1,eqclause2,eqgoal,timelimit,weight=300,sos=200,extraclauses=""):
#Checks with Prover9 if eqclause1 & eqclause2 imply eqgoal, with defined time limit,amx weight, and sos limit
    task = (f"""assign(max_seconds, {timelimit}).
    assign(max_megs, 2000).
    assign(max_weight, {weight}).
    assign(sos_limit, {sos}).
    formulas(sos). {eqclause1}. {eqclause2}. {extraclauses} end_of_list.
    formulas(goals). {eqgoal}. end_of_list.""")
    prover9_out = subprocess.run(PROVER9, input=task, text=True, capture_output=True).stdout
    if "(max_proofs)" in str(prover9_out):
        return True
    return None

def countermodeltoeq(eqclause1,eqclause2,eqgoal,timelimit,extraclauses="",selection_measure=3,skolems_last="set(skolems_last).",
                     start_size=2,end_size=-1,increment=1,iterate="all",time_per_size=-1):
#Checks with Mace4 if there is a model satisfying eqclause1 & eqclause2 but not eqgoal, with defined time limit and selection measure
    task = rf"""
    assign(max_seconds, {timelimit}).
    assign(max_seconds_per, {time_per_size}).
    assign(start_size, {start_size}).
    assign(end_size, {end_size}).
    assign(increment, {increment}).
    assign(iterate, {iterate}).
    assign(max_megs, 2000).
    assign(selection_measure, {selection_measure}).
    {skolems_last}
    formulas(sos). {eqclause1}. {eqclause2}. {extraclauses} end_of_list.
    formulas(goals). {eqgoal}. end_of_list."""
    mace4_out = subprocess.run(MACE4, input=task, text=True, capture_output=True).stdout
    if "(max_models)" in str(mace4_out):
        return True
    return None

In [4]:
def findantiimplication(eqassumption,eqidlist,eqgoal,extraclauses="",time_implication=5,weight=300,sos=200,time_model=60,
                        selection_measure=3,skolems_last="set(skolems_last).",start_size=2,end_size=-1,time_per_size=-1,
                        increment=1,iterate="all",verbose=100,breakiffound=True):
#We find the anti-implications to eqgoal, from eqassumption and each equation in eqidlist, with extraclauses if wanted.
#Example of extraclauses: extra_clauses = "x*y = x*z -> y = z. exists a all x (x*a = x)."
#For each equation in eqidlist we apply Prover9 time_implication seconds with the chosen max_weight and sos_limit,
#then Mace4 time_model seconds with the chosen selection_measure, skolems_last, start size, end size, time per size, increment
#and iterate.
#Returns (antieq,implyeq,unknowneq), with antieq the equation that doesn't imply eqgoal,
#implyeq those equations which do imply eqgoal, and unknowneq those for which the computation is inconclusive
#If breakiffound=True, only the first anti-implication found is returned

    numeq = len(eqidlist)
    timepereq = time_implication + time_model
    print(f"""The number of equations to try is {numeq}.
The maximum time per equation is {timepereq}s. The maximum gobal time is {round(numeq*timepereq/3600,2)}h.
Computation started at {time.strftime("%Y-%m-%d %H:%M:%S", time.localtime())}""")

    if type(eqassumption)==int: #If we receive the equatoin id instead of the equation
        eqassumption = str(find_equation_id.Equation.from_id(eqassumption))
    if type(eqgoal)==int:
        eqgoal = str(find_equation_id.Equation.from_id(eqgoal))
    eqassumption = eqassumption.replace('◇','*')
    eqgoal = eqgoal.replace('◇','*')
    implyeq = []
    antieq = []
    unknowneq = []
    time1=time.time()
    count=0
    for idnum in eqidlist:
        if count!=0 and count%verbose==0:
            time2=time.time()
            timeelapsed = round((time2-time1)/60,2)
            time1=time2
            print(f"{count} equations evaluated, in {timeelapsed}min")
        count+=1
        eq=find_equation_id.Equation.from_id(idnum)
        eqstr=str(eq).replace('◇','*')
        res = implicationtoeq(eqassumption,eqstr,eqgoal,time_implication,weight,sos,extraclauses)
        if res:
            implyeq.append(eq)
            if verbose==1:
                print(f"Implication found with equation {idnum}")
            continue
        res = countermodeltoeq(eqassumption,eqstr,eqgoal,time_model,extraclauses=extraclauses,
                               selection_measure=selection_measure,start_size = start_size, end_size = end_size,
                               time_per_size = time_per_size, increment = increment, iterate = iterate)
        if res:
            antieq.append(eq)
            print(f"Antiimplication found with equation {idnum}!")
            if breakiffound: break
            continue
        unknowneq.append(eq)
        print(f"{eq.id} inconclusive")
    print(f"""Finished at {time.strftime("%Y-%m-%d %H:%M:%S", time.localtime())}:
{len(antieq)} antiimplications, {len(implyeq)} implications, {len(unknowneq)} inconclusive".
    Inconclusive computation: {[eq.id for eq in unknowneq]}""")
    return (antieq,implyeq,unknowneq)

In [5]:
def findantiimplicationpairs(eqassumption,eqidlist,eqgoal,extraclauses="",time_implication=5,weight=300,sos=200,time_model=60,
                        selection_measure=3,skolems_last="set(skolems_last).",start_size=2,end_size=-1,time_per_size=-1,
                        increment=1,iterate="all",verbose=100,breakiffound=True):
#We find the anti-implications to eqgoal, from eqassumption and each pair of equations in eqidlist, with extraclauses if wanted.
#Example of extraclauses: extra_clauses = "x*y = x*z -> y = z. exists a all x (x*a = x)."
#For each pair of equations in eqidlist we apply Prover9 time_implication seconds with the chosen max_weight and sos_limit,
#then Mace4 time_model seconds with the chosen selection_measure, skolems_last, start size, end size, time per size, increment
#and iterate.
#Returns (antieq,implyeq,unknowneq), with antieq the pairs of equations that don't imply eqgoal,
#implyeq those pairs of equations which do imply eqgoal, and unknowneq those for which the computation is inconclusive
#If breakiffound=True, only the first anti-implication found is returned

    numpairs = sum(1 for _ in itertools.combinations(eqidlist,2))
    timepereq = time_implication + time_model
    print(f"""The number of pairs to try is {numpairs}.
The maximum time per pair is {timepereq}s. The maximum gobal time is {round(numpairs*timepereq/3600,2)}h.
Computation started at {time.strftime("%Y-%m-%d %H:%M:%S", time.localtime())}""")

    if type(eqassumption)==int: #If we receive the equation id instead of the equation
        eqassumption = str(find_equation_id.Equation.from_id(eqassumption))
    if type(eqgoal)==int:
        eqgoal = str(find_equation_id.Equation.from_id(eqgoal))
    eqassumption = eqassumption.replace('◇','*')
    eqgoal = eqgoal.replace('◇','*')
    implyeq = []
    antieq = []
    unknowneq = []
    time1=time.time()
    count=0
    for pairids in itertools.combinations(eqidlist,2):
        if count!=0 and count%verbose==0:
            time2=time.time()
            timeelapsed = round((time2-time1)/60,2)
            time1=time2
            print(f"{count} pairs of equations evaluated, in {timeelapsed}min")
        count+=1
        idnum1, idnum2 = pairids[0], pairids[1]
        eq1=find_equation_id.Equation.from_id(idnum1)
        eq2=find_equation_id.Equation.from_id(idnum2)
        eq1str=str(eq1).replace('◇','*')
        eq2str=str(eq2).replace('◇','*')
        extra = f"{eq2str}. {extraclauses}"
        res = implicationtoeq(eqassumption,eq1str,eqgoal,time_implication,weight,sos,extraclauses=extra)
        if res:
            implyeq.append(pairids)
            continue
        res = countermodeltoeq(eqassumption,eq1str,eqgoal,time_model,extraclauses=extra,
                               selection_measure=selection_measure,start_size = start_size, end_size = end_size,
                               time_per_size = time_per_size, increment = increment, iterate = iterate)
        if res:
            antieq.append(pairids)
            print(f"Antiimplication found with pair {pairids}!")
            if breakiffound: break
            continue
        unknowneq.append(pairids)
        print(f"{pairids} inconclusive")
    print(f"""Finished at {time.strftime("%Y-%m-%d %H:%M:%S", time.localtime())}:
{len(antieq)} antiimplications, {len(implyeq)} implications, {len(unknowneq)} inconclusive.
    Inconclusive computation: {unknowneq}""")
    return (antieq,implyeq,unknowneq)

In [6]:
completelyunknowncandidates = [48217520, 48217671, 58095440, 73169078, 73169229, 102743259, 102745815, 102749116, 113067945, 113071354, 121884950, 122693826, 122697948]

In [7]:
%%time
anti,imply,unknown = findantiimplication(4369,completelyunknowncandidates,543,extraclauses="",time_implication=60,weight=300,sos=200,time_model=60,
                        selection_measure=3,skolems_last="set(skolems_last).",verbose=1,breakiffound=False)

The number of equations to try is 13.
The maximum time per equation is 120s. The maximum gobal time is 0.43h.
Computation started at 2024-12-21 22:58:20
Implication found with equation 48217520
1 equations evaluated, in 0.0min
Implication found with equation 48217671
2 equations evaluated, in 0.03min
Implication found with equation 58095440
3 equations evaluated, in 0.17min
Implication found with equation 73169078
4 equations evaluated, in 0.01min
Implication found with equation 73169229
5 equations evaluated, in 0.0min
Implication found with equation 102743259
6 equations evaluated, in 0.02min
Implication found with equation 102745815
7 equations evaluated, in 0.01min
Implication found with equation 102749116
8 equations evaluated, in 0.0min
Implication found with equation 113067945
9 equations evaluated, in 0.01min
Implication found with equation 113071354
10 equations evaluated, in 0.0min
Implication found with equation 121884950
11 equations evaluated, in 0.0min
Implication found w

In [8]:
%%time
antiHN,implyHN,unknownHN = findantiimplication(4369,completelyunknowncandidates,42323216,extraclauses="",time_implication=60,weight=300,sos=200,time_model=0,
                        selection_measure=3,skolems_last="set(skolems_last).",verbose=1,breakiffound=False)

The number of equations to try is 13.
The maximum time per equation is 60s. The maximum gobal time is 0.22h.
Computation started at 2024-12-21 22:58:40
Implication found with equation 48217520
1 equations evaluated, in 0.0min
Implication found with equation 48217671
2 equations evaluated, in 0.02min
Implication found with equation 58095440
3 equations evaluated, in 0.16min
Implication found with equation 73169078
4 equations evaluated, in 0.0min
Implication found with equation 73169229
5 equations evaluated, in 0.0min
Implication found with equation 102743259
6 equations evaluated, in 0.01min
Implication found with equation 102745815
7 equations evaluated, in 0.01min
Implication found with equation 102749116
8 equations evaluated, in 0.0min
Implication found with equation 113067945
9 equations evaluated, in 0.01min
Implication found with equation 113071354
10 equations evaluated, in 0.0min
Implication found with equation 121884950
11 equations evaluated, in 0.0min
Implication found wit

In [ ]:
%%time
inconclusive=dict.fromkeys(completelyunknowncandidates)
for i,candidate in enumerate(completelyunknowncandidates):
    print(f"Starting with candidate {candidate}, {i+1} of {len(completelyunknowncandidates)} to evaluate")
    anti,imply,unknown = findantiimplication(candidate,range(2,5001),42323216,extraclauses="",time_implication=60,weight=300,sos=200,time_model=60,
                        selection_measure=3,skolems_last="set(skolems_last).",verbose=100,breakiffound=True)
    inconclusive[candidate]=unknown
print(inconclusive)

Starting with candidate 48217520, 1 of 13 to evaluate
The number of equations to try is 4999.
The maximum time per equation is 120s. The maximum gobal time is 166.63h.
Computation started at 2024-12-21 23:01:09
8 inconclusive
47 inconclusive
50 inconclusive
53 inconclusive
99 inconclusive
100 equations evaluated, in 10.09min
104 inconclusive
151 inconclusive
200 equations evaluated, in 4.04min
203 inconclusive
255 inconclusive
264 inconclusive
300 equations evaluated, in 6.07min
400 equations evaluated, in 0.02min
411 inconclusive
414 inconclusive
417 inconclusive
419 inconclusive
420 inconclusive
427 inconclusive
429 inconclusive
430 inconclusive
436 inconclusive
437 inconclusive
466 inconclusive
467 inconclusive
473 inconclusive
474 inconclusive
476 inconclusive
500 equations evaluated, in 31.15min
503 inconclusive
511 inconclusive
513 inconclusive
562 inconclusive
600 equations evaluated, in 8.08min
614 inconclusive
619 inconclusive
620 inconclusive
622 inconclusive
630 inconclusive

In [5]:
completelyunknowncandidates = [48217520, 48217671, 58095440, 73169078, 73169229, 102743259, 102745815, 102749116, 113067945, 113071354, 121884950, 122693826, 122697948]